In [1]:
import re
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import LatentDirichletAllocation
import pandas as pd

In [149]:
import sqlite3

# Connect to the SQLite database (or create it if it doesn't exist)
conn = sqlite3.connect('email_database.db')
cursor = conn.cursor()

# Create tables
cursor.execute('''CREATE TABLE IF NOT EXISTS ECT
             (name TEXT, email TEXT, PRIMARY KEY(name))''')

cursor.execute('''CREATE TABLE IF NOT EXISTS Enron
             (name TEXT, email TEXT, PRIMARY KEY(name))''')

cursor.execute('''CREATE TABLE IF NOT EXISTS EES
             (name TEXT, email TEXT, PRIMARY KEY(name))''')

cursor.execute('''CREATE TABLE IF NOT EXISTS USA
             (name TEXT, email TEXT, PRIMARY KEY(name))''')

cursor.execute('''CREATE TABLE IF NOT EXISTS EU
             (name TEXT, email TEXT, PRIMARY KEY(name))''')

cursor.execute('''CREATE TABLE IF NOT EXISTS High_ranking
             (name TEXT, email TEXT, PRIMARY KEY(name))''')

# Define methods
def insert_or_update(table_name, name, email):
    try:
        conn = sqlite3.connect('email_database.db')
        cursor = conn.cursor()
        cursor.execute(f"INSERT OR REPLACE INTO {table_name} (name, email) VALUES (?, ?)", (name, email))
        conn.commit()
    except sqlite3.Error as e:
        print(f"An error occurred: {e}")

def get_by_name(table_name, name):
    try:
        conn = sqlite3.connect('email_database.db')
        cursor = conn.cursor()
        cursor.execute(f"SELECT name, email FROM {table_name} WHERE name = ?", (name,))
        result = cursor.fetchone()
        conn.close()
        return True
    except sqlite3.Error as e:
        print(f"An error occurred: {e}")
        return False

def get_by_email(table_name, email):
    try:
        conn = sqlite3.connect('email_database.db')
        cursor = conn.cursor()
        cursor.execute(f"SELECT name, email FROM {table_name} WHERE email = ?", (email,))
        result = cursor.fetchone()
        conn.close()
        return True
    except sqlite3.Error as e:
        print(f"An error occurred: {e}")
        return False

def get_all_names(table_name):
    try:
        conn = sqlite3.connect('email_database.db')
        cursor = conn.cursor()
        cursor.execute(f"SELECT name FROM {table_name}")
        names = cursor.fetchall()
        conn.close()
        return set([name[0] for name in names]) 
    except sqlite3.Error as e:
        print(f"An error occurred: {e}")
        return set()

def get_all_emails(table_name):
    try:
        conn = sqlite3.connect('email_database.db')
        cursor = conn.cursor()
        cursor.execute(f"SELECT email FROM {table_name}")
        emails = cursor.fetchall()
        conn.close()
        return set([email[0] for email in emails])
    except sqlite3.Error as e:
        print(f"An error occurred: {e}")
        return None

# Example usage
insert_or_update('ECT', 'John Doe', 'john.doe@example.com')
print(get_by_name('ECT', 'John Doe'))

# Close the connection
conn.close()


True


In [250]:
import string

keywords = {
    'legal': {
        'arbitration agreement', 'breach of contract', 'civil litigation', 'confidential information', 
        'copyright infringement', 'criminal law', 'defamation lawsuit', 'employment contract', 
        'fiduciary duty', 'intellectual property', 'jurisdictional issue', 'legal counsel', 
        'negligence claim', 'patent infringement', 'privacy policy', 'property rights', 
        'public domain', 'real estate transaction', 'statute of limitations', 'tort law', 
        'trade secret misappropriation', 'trial court', 'unfair competition', 'validity of contract', 
        'will and testament', 'witness testimony', 'agency agreement', 'breach of duty', 
        'civil rights violation', 'contractual dispute', 'disclaimer of liability', 
        'employment discrimination', 'fraudulent misrepresentation', 'indemnification clause', 
        'judicial precedent', 'legal notice', 'negligent act', 'personal injury lawsuit', 
        'property ownership', 'public policy', 'restraining order', 'statutory law', 
        'tortious interference', 'trade regulation', 'trust agreement', 'valid contract', 
        'warranty disclaimer', 'will contest', 'work-for-hire agreement', 'acquisition agreement','law',
        'court','lawsuit', "court", "lawsuit", "attorney", "legal", "judge", "jurisdiction", "litigation",
        "plaintiff", "defendant", "verdict", "appeal", "settlement", "deposition", "evidence", "crime",
        "trial", "offense", "prosecution", "defense", "law", "lawyer", "case", "contract", "agreement",
        "arbitration", "bankruptcy", "civil", "criminal", "discovery", "injunction", "legal system",
        "legislation", "liability", "mediation", "ordinance", "regulation", "subpoena", "testimony", "tort", "waiver",
        "contract", "agreement", "court", "lawsuit", "legal", "lawyer", "case", "brief", "claim", "complaint",
        "dispute", "judgment", "petition", "settlement", "litigation", "hearing", "appeal", "witness", "testimony", 
        "evidence", "arbitration", "mediation", "deposition", "damages", "injunction", "verdict", "defense", 
        "plaintiff", "defendant", "guilty", "not guilty", "sentence", "appeal", "jurisdiction", "law firm", 
        "legal counsel", "legal advice", "legal action", "legal department", "legal issue", "legal matter", "legal opinion",
        "court date", "legal document", "legal procedure", "legal system", "legal team", "legal terminology", 
        "legal writing", "legalities", "legalize", "legally binding", "litigation process", "law enforcement", 
        "law enforcement agency", "law enforcement officer", "lawful", "lawlessness", "lawsuit settlement", "lawful arrest", 'analysis'
    },
    'financial': {
        'asset management', 'balance sheet', 'capital gains', 'cash flow', 'commercial banking', 
        'credit rating', 'currency exchange', 'debit card', 'dividend yield', 'equity financing', 
        'exchange rate', 'financial analyst', 'fiscal policy', 'forex trading', 'hedge fund', 
        'income statement', 'insurance policy', 'investment portfolio', 'liquidity ratio', 
        'mortgage loan', 'mutual fund', 'net income', 'overdraft protection', 'payroll processing', 
        'personal finance', 'retirement planning', 'risk management', 'stock market', 
        'tax deduction', 'venture capital', 'wealth management', 'yield curve', 
        'account reconciliation', 'annual percentage rate', 'audit trail', 'bankruptcy filing', 
        'capital expenditure', 'collateralized debt obligation', 'credit limit', 'debit balance', 
        'earnings per share', 'financial planner', 'foreign exchange market', 'government bond', 
        'income tax return', 'insurance premium', 'investment banker', 'liability insurance', 
        'money market account', 'mutual fund expense ratio', 'net worth', 'payment processing',
        'forecast', 'money', 'investment', 'bank', 'bankruptcy', "finance", "financial", "investment", 
        "banking", "budget", "capital", "credit", "debt", "equity", "income", "interest", 
        "loan", "mortgage", "profit", "revenue", "risk", "asset", "liability", "audit", 
        "bankruptcy", "bond", "cash flow", "currency", "inflation", "market", "stock", 
        "tax", "trade", "transaction", "wealth", "hedge fund", "mutual fund", "stock exchange", "insurance", "pension", 
        "retirement", "savings", "venture capital", 'pay', 'buy', 'price', 'cost', 'range', 'dollar', 'trading',
        "financial", "finance", "investment", "bank", "banking", "account", "transaction", "payment", "deposit", 
        "withdrawal", "credit", "debit", "loan", "mortgage", "interest", "balance", "statement", "credit card", "debit card", 
        "insurance", "policy", "claim", "coverage", "premium", "tax", "taxes", "taxation", "taxpayer", "taxable", "tax-exempt", 
        "income", "expense", "profit", "loss", "revenue", "budget", "forecast", "audit", "accountant", "financial advisor", 
        "financial planner", "investment advisor", "investment firm","annual income", "bank account", "bank statement", 
        "bill payment", "credit score", "debit card transaction", "financial advisor consultation", "financial investment", 
        "financial management", "financial planner appointment", "financial statement", "income tax", "insurance claim", 
        "insurance coverage", "insurance policy", "investment advice", "investment opportunity", "investment portfolio", 
        "loan application", "mortgage agreement", "retirement fund", "tax deduction", "tax refund", "tax return", "taxable income", 'transmit', 'million', 'balance', 'financing', 'analysis', 'spending', 'spend', "$", "report",
    },
    'business': {
        'brand identity', 'competitive advantage', 'consumer behavior', 'corporate governance', 'deal', 'partnership','trade', "$"
        'purchase', "sold", 'sell','amount', 'dollar','trading',
        'customer relationship management', 'distribution channel', 'entrepreneurship', 
        'franchise agreement', 'human resource management', 'industry analysis', 'innovation strategy', 
        'key performance indicator', 'marketing strategy', 'networking event', 'operational efficiency', 
        'partnership agreement', 'product development', 'quality control', 'revenue stream', 
        'strategic alliance', 'supply chain management', 'target market', 'value proposition', 
        'business model canvas', 'business process reengineering', 'cash flow statement', 
        'core competency', 'customer retention', 'diversification strategy', 'financial projection', 
        'intellectual capital', 'market segmentation', 'organizational culture', 'performance appraisal', 
        'product differentiation', 'risk assessment', 'sales forecast', 'strategic planning', 
        'sustainable business practices', 'transactional analysis', 'value chain analysis', 
        'business continuity plan', 'business ethics', 'cost-benefit analysis', 'customer satisfaction', 
        'economic recession', 'financial statement analysis', 'market research', 'operational risk','business', 
        'company', 'industry', 'corporate', "business", "company", "corporation", "industry", "management", 
        "marketing", "sales", "advertising", "branding", "customer", "product", "service", "market", "competition", 
        "strategy", "finance", "investment", "profit", "revenue", "cost", "budget", "employee", "leadership", 
        "negotiation", "partnership", "merger", "acquisition", "supply chain", "logistics", "innovation", "technology", 
        "entrepreneurship", "start-up", "small business", 'business',"corporation", "organization", "enterprise", "industry", 
        "market", "product", "service", "customer", "client", "consumer", "supplier", "vendor", "partner", "contractor", "employee", 
        "employer", "manager", "executive", "director", "CEO", "CFO", "COO", "CTO", "board", "meeting", "conference", "presentation", 
        "proposal", "strategy", "plan", "goal", "objective", "performance", "profit", "revenue", "growth", "expansion", "merger", 
        "acquisition", "partnership", "joint venture","business cost", "business growth", "business plan", "business proposal", 
        "business strategy", "buying decision", "client meeting", "company culture", "company policy", "competitive market", 
        "consumer demand", "corporate culture", "corporate governance", "corporate responsibility", "customer feedback", "customer service", 
        "employee benefits", "employee engagement", "employee evaluation", "employee performance", "employee satisfaction", "executive decision", 
        "financial performance", "financial report", "investment opportunity", "marketing campaign", "meeting agenda", "new business", "performance evaluation", 
        "product launch", "profit margin", "project deadline", "sales forecast", "sales target", "team collaboration", "teamwork", "vendor agreement", 'offer', 'project', 'deal', 'report', 'market'
    },
    # "Health": {
    #     'health', 'healthcare', 'medical', 'medicine', 'doctor', 'physician', 'patient', 'hospital', 'clinic', 'nurse', 'treatment', 'therapy', 'surgery', 'disease', 'illness', 'injury', 'prevention', 'wellness', 'nutrition', 'diet', 'exercise', 'mental health','public health', 'pharmaceutical', 'vaccine', 'research', 'study', 'laboratory', 'technology', 'telemedicine', 'pandemic', 'epidemic', 'insurance'
    # },
    # "Politics": {
    #     'politics', 'political', 'government', 'democracy', 'election', 'campaign', 'candidate', 'party', 'policy', 'legislation', 'law', 'constitution', 'administration', 'congress', 'senate', 'house of representatives', 'president', 'vice president', 'cabinet', 'judiciary', 'supreme court', 'international relations', 'diplomacy', 'negotiation', 'treaty', 'alliance', 'conflict', 'war', 'peace', 'security', 'defense'
    # },
    # "Environment": {
    #     'environment', 'environmental', 'climate', 'climate change', 'global warming', 'pollution', 'conservation', 'sustainability', 'ecosystem', 'biodiversity', 'habitat', 'natural resources', 'renewable energy', 'clean energy', 'carbon footprint', 'emissions', 'recycling', 'waste management', 'deforestation', 'endangered species', 'wildlife', 'ocean', 'air', 'water', 'soil', 'green technology', 'environmental policy', 'carbon'
    # },
    # "Technology": {
    #     'technology', 'tech', 'digital', 'innovation', 'internet', 'software', 'hardware', 'computer', 'device', 'gadget', 'artificial intelligence', 'AI', 'machine learning', 'data', 'analytics', 'cloud computing', 'cybersecurity', 'network', 'social media', 'website', 'app', 'mobile', 'communication', 'automation', 'robotics', 'virtual reality', 'augmented reality', 'blockchain', 'cryptocurrency', 'gaming', 'e-commerce'
    # }

    
}

def assign_labels(text):
    # Remove punctuation
    translator = str.maketrans('', '', string.punctuation)
    text = text.translate(translator)
    
    labels = []
    for topic, kw_set in keywords.items():
        if any(kw in kw_set for kw in text.split()):
            labels.append(topic)
    if '$' in text and ('financial' not in labels or 'business' not in labels):
        if 'financial' not in labels:
            labels.append('financial')
        if 'business' not in labels:
            labels.append('business')
    if not labels:
        labels.append('general')
    return labels

In [128]:
# Function to perform topic modeling
def topic_modeling(text):
    return assign_labels(text)

In [129]:
import spacy
import re
nlp = spacy.load("en_core_web_sm")

def rule_based_analysis(text):
    entities = extract_entities_spacy(text)
    # print("Named Entities:", entities)  

    ssn_list = extract_ssn(text)
    # print("SSN List:", ssn_list)

    phone_list = extract_phone_numbers(text)
    # print("Phone Numbers:", phone_list)

    email_list = extract_emails(text)
    # print("Emails:", email_list)

    zip_code_list = extract_zip_codes(text)
    # print("Zip Codes:", zip_code_list)

    address_list = extract_addresses(text)
    # print("Addresses:", address_list)

    credit_card_list = extract_credit_card_numbers(text)
    # print("Credit Card Numbers:", credit_card_list)

    data = {'Named Entities': entities, 'SSN': ssn_list, 'Phone Numbers': phone_list, 'Emails': email_list, 'Zip Codes': zip_code_list, 'Addresses': address_list, 'Credit Card Numbers': credit_card_list}
    return data

# Extract named entities using spaCy
def extract_entities_spacy(text):
    doc = nlp(text)
    entities = []
    for ent in doc.ents:
        entities.append((ent.text, ent.label_))
    return entities   

def extract_ssn(text):
    ssn_list = []
    ssn_pattern = re.compile(r'\b(?!000|666|9\d{2})\d{3}-(?!00)\d{2}-(?!0000)\d{4}\b')
    ssn_matches = ssn_pattern.findall(text)
    for match in ssn_matches:
        ssn_list.append(match)
    return ssn_list

def extract_phone_numbers(text):
    phone_list = []
    phone_pattern = re.compile(r'\(?\d{3}\)?[-.\s]?\d{3}[-.\s]?\d{4}')
    phone_matches = phone_pattern.findall(text)
    for match in phone_matches:
        phone_list.append(match)
    return phone_list

def extract_emails(text):
    email_list = []
    email_pattern = re.compile(r'\b[A-Za-z0-9._%+-]+@[A-Za-z0-9.-]+\.[A-Z|a-z]{2,}\b')
    email_matches = email_pattern.findall(text)
    for match in email_matches:
        email_list.append(match)
    return email_list

def extract_zip_codes(text):
    zip_code_list = []
    zip_code_pattern = re.compile(r'\b\d{5}(?:-\d{4})?\b')
    zip_code_matches = zip_code_pattern.findall(text)
    for match in zip_code_matches:
        zip_code_list.append(match)
    return zip_code_list

def extract_addresses(text):
    address_list = []
    address_pattern = re.compile(r'\d{1,5}\s\w.\s(\b\w*\b\s){1,2}\w*\.')
    address_matches = address_pattern.findall(text)
    for match in address_matches:
        address_list.append(match)
    return address_list

def extract_credit_card_numbers(text):
    credit_card_list = []
    credit_card_pattern = re.compile(r'\b(?:\d[ -]*?){13,16}\b')
    credit_card_matches = credit_card_pattern.findall(text)
    for match in credit_card_matches:
        credit_card_list.append(match)
    return credit_card_list
    

In [130]:
# Define a comprehensive dictionary of sensitive terms
# Expanded sensitive dictionary with at least 50 terms in each category
sensitive_dictionary = {
    'PII': [
        'social security number', 'ssn', 'credit card number', 'passport number', 'driver\'s license number',
        'bank account number', 'date of birth', 'mother\'s maiden name', 'medical record number', 'health insurance number',
        'financial account number', 'taxpayer identification number', 'alien registration number', 'biometric information',
        'digital signature', 'full name', 'home address', 'email address', 'phone number', 'login credentials', 'personal identification number',
        'place of birth', 'phone number', 'email address', 'home address', 'full name', 'date of birth', "ip:",
    ],
    'QID': [
    'gender', 'gender identity', 'sexual orientation', 'race', 'ethnicity', 'nationality', 'religion', 'marital status',
    'disability status', 'veteran status', 'political affiliation', 'language spoken', 'education level', 'occupation'
    ],
    'places' : [
    ]
}


# Function to perform dictionary-based matching
def dictionary_based_matching(text):
    # Remove punctuation
    translator = str.maketrans('', '', string.punctuation)
    text = text.translate(translator)

    tokenized_text = text.split()

    matches = set()
    for category, terms in sensitive_dictionary.items():
        for term in terms:
            if term in tokenized_text:
                matches.add(category)
                
    return matches

In [131]:
# Function to perform content analysis on an email
def content_analysis(text):
    data = rule_based_analysis(text)
    categorys =  dictionary_based_matching(text)
    data['categories'] = list(categorys)
    return data

In [170]:
def is_subject_legal(email_details):
    if 'legal' in email_details['topics']:
        print("Legal subject detected!")
        return True
    return False   

def is_subject_financial(email_details):
    if 'financial' in email_details['topics']:
        print("Financial subject detected!")
        return True
    return False

def is_subject_business(email_details):
    if 'business' in email_details['topics']:
        print("Business subject detected!")
        return True
    return False

def is_transfer_outside_corp(email_details):
    anyOne = True
    if 'enron.com' in email_details['From']:
        for person in email_details['To']:
            if 'enron.com' not in person:
                anyOne = False

    if anyOne == True:
        return False            

    if email_details['X-From'] in ECT_employers or email_details['X-From'] in EES_employers or email_details['X-From'] in Enron_employers:  
        for person in email_details['X-To']:
            if person not in ECT_employers or person not in EES_employers or person not in Enron_employers:
                print("Transfer outside corporation detected2!," + person + "not in ECT_employers or EES_employers or Enron_employers")
                return True

    if email_details['From'] in ECT_employers or email_details['From'] in EES_employers or email_details['From'] in Enron_employers:  
        for person in email_details['To']:
            if person not in ECT_employers or person not in EES_employers or person not in Enron_employers:
                print("Transfer outside corporation detected3!")
                return True            

    return False

def is_contains_pii_or_qid(email_details):
    if 'PII' in email_details['data']['categories'] or 'QID' in email_details['data']['categories']:
        print("Contains PII or QID!")
        return True

    if len(email_details['data']['SSN']) > 0 or len(email_details['data']['Phone Numbers']) > 0 or len(email_details['data']['Zip Codes']) > 0 or len(email_details['data']['Addresses']) > 0 or len(email_details['data']['Credit Card Numbers']) > 0:
        print("Contains PII or QID!")
        return True    
    return False

def is_transfer_outside_ECT(email_details):
    if email_details['X-From'] in ECT_employers or email_details['From'] in EES_employers:
        for person in email_details['X-To']:
            if person not in ECT_employers:
                print("Transfer outside ECT detected!")
                return True
    return False   

def is_transfer_between_vps_directors_ceos(email_details):
    if email_details['X-From'] in high_ranking_employees or email_details['From'] in high_ranking_employees:
        for person in email_details['X-To']:
            if person in high_ranking_employees:
                return True

        for person in email_details['To']:
            if person in high_ranking_employees:
                return True       
    return False    

def is_transfer_between_ect_and_ees(email_details):
    if (email_details['X-From'] in ECT_employers or email_details['From'] in ECT_employers):
        for person in email_details['X-To']:
            if person in EES_employers:
                print("Transfer between ECT and EES detected!")
                return True

        for person in email_details['To']:
            if person in EES_employers:
                print("Transfer between ECT and EES detected!")
                return True               
        
    return False  

def is_transfer_between_eu_and_usa(email_details):
    # Extract sender's and receiver's email addresses
    sender_email = email_details['From']
    receiver_emails = email_details['To']

    # Check if sender is from EU and receiver is from USA
    sender_from_eu = sender_email.endswith('.eu')
    receiver_from_usa = any(receiver.endswith('.us') for receiver in receiver_emails)

    # Check if sender is from USA and receiver is from EU
    sender_from_usa = sender_email.endswith('.us')
    receiver_from_eu = any(receiver.endswith('.eu') for receiver in receiver_emails)

    if (sender_from_eu and receiver_from_usa) or (sender_from_usa and receiver_from_eu):
        print("Transfer between EU and USA detected!")
        return True

    # check by data
    if (email_details['X-From'] in USA_employers or  email_details['From'] in USA_employers):
        for person in email_details['X-To']:
            if person in EU_employers:
                print("Transfer between EU and USA detected!")
                return True

        for person in email_details['To']:
            if person in EU_employers:
                print("Transfer between EU and USA detected!")
                return True
    
    return False      

In [162]:
def check_rules(email_details): # list of broken rules
    broken_rules = []

    #Policy Group #1 – Internal Data Sharing Limitations and Geo-fencing

    # Rule #1 – Legal related emails cannot be transferred between ECT and EES within the corporation
    if is_subject_legal(email_details) and is_transfer_between_ect_and_ees(email_details):
        print("Rule #1 group 1 – Legal related emails cannot be transferred between ECT and EES within the corporation")
        broken_rules.append("1.1")

    #Rule #2 – financial data cannot be transferred between EU and USA
    if is_subject_financial(email_details) and is_transfer_between_eu_and_usa(email_details):    
        print("Rule #2 group 1 – financial data cannot be transferred between EU and USA")
        broken_rules.append("1.2")

    #Rule #3 – no business or financial emails/documents can leave corporation perimeter    
    if (is_subject_business(email_details) or is_subject_financial(email_details)) and is_transfer_outside_corp(email_details):
        print("Rule #3 group 1 – no business or financial emails/documents can leave corporation perimeter")
        broken_rules.append("1.3")

    # #Policy Group #2 – Privacy and Sensitivity

    #Rule #1 – emails containing finance information with PII or QID must not leave ECT company    
    if is_subject_financial(email_details) and is_contains_pii_or_qid(email_details) and is_transfer_outside_ECT(email_details):
        print("Rule #1 group 2 – emails containing finance information with PII or QID must not leave ECT company")
        broken_rules.append("2.1")

    #Rule #2 – sensitive business information can be passed only between VPs, Directors, and C-level employees    
    if is_subject_business(email_details) and not is_transfer_between_vps_directors_ceos(email_details):
        print("Rule #2 group 2 – sensitive business information can be passed only between VPs, Directors, and C-level employees")
        broken_rules.append("2.2")

    #Rule #3 – block mails containing PII or number of QIDs sent outside the corporation.
    if is_contains_pii_or_qid(email_details) and is_transfer_outside_corp(email_details):
        print("Rule #3 group 2 – block mails containing PII or number of QIDs sent outside the corporation.")
        broken_rules.append("2.3")

    verdict = True
    if len(broken_rules) > 0:
        verdict = False
    return verdict , broken_rules   

In [262]:
def process_email(email):
    email_string = ""
    if email["From"] is not None:
        email_string += "From: " + email["From"] + "\n"
    if email["To"] is not None:
        email_string += "To: " + email["To"] + "\n"
    if email["Subject"] is not None:
        email_string += "Subject: " + email["Subject"] + "\n"
    if email["email_body"] is not None:
        email_string += "Mail Body: " + email["email_body"]

    email_details = {
    "email_string": email_string if email_string is not None else "",
    "From": email["From"] if email["From"] is not None else "",
    "To": email["To"].split(', ') if email["To"] is not None else "",
    "X-From": email["X-From"] if email["X-From"] is not None else "",
    "X-To": email["X-To"].split(', ') if email["X-To"] is not None else [],
    "data": content_analysis(email_string) if email_string is not None else {},
    "topics": topic_modeling(email_string) if email_string is not None else {},
    }


    # print("Email Details:\n", email_details)
    # for key, value in email_details.items():
    #     print(key, ":", value)
    #     print("--------------------")


    verdict, broken_rules =  check_rules(email_details)

    print("Their verdict: " + str(email['verdict']) + " vs our verdict: " + str(verdict)) 
    print("Their Broken Rules: " + ', '.join(email['violated_rules']) + " vs our broken rules: " + ', '.join(broken_rules))
    return verdict
    


In [259]:
Enron_employers = set()
ECT_employers = set()
EES_employers = set()
USA_employers = set()
EU_employers = set()
high_ranking_employees = {
    "Kenneth Lay",
    "Jeffrey Skilling",
    "Andrew Fastow",
    "Richard Causey",
    "Rebecca Mark-Jusbasche",
    "Lou Pai",
    "Forrest Hoglund",
    "Dennis Ulak",
    "Jeffrey Sherrick",
    "Richard Gallagher",
    "Kenneth Rice",
    "J. Clifford Baxter",  # Corrected with comma and spaces
    "Sherron Watkins",
    "Jim Derrick",
    "Mark Koenig",
    "Joan Foley",
    "Richard Kinder",
    "Greg Whalley",
    "Jeff McMahon",
    "Robert A. Belfer",  # Corrected with period
    "Norman P. Blake Jr",
    "Ronnie C. Chan",
    "John H. Duncan",
    "Wendy L. Gramm",
    "Ken L. Harrison",
    "Robert K. Jaedicke",
    "Charles A. LeMaistre",
    "John Mendelsohn",
    "Jerome J. Meyer",
    "Richard K. Gallagher",
    "Paulo V. Ferraz Pereira",
    "Frank Savage",
    "John A. Urquhart",
    "John Wakeham",
    "Herbert S. Winokur Jr",
    "Phillip K Allen",  # Ensure consistent format
}


def loadFromDB():
    Enron_employers_names = get_all_names("Enron")
    ECT_employers_names = get_all_names("ECT")
    EES_employers_names = get_all_names("EES")
    USA_employers_names = get_all_names("USA")
    EU_employers_names = get_all_names("EU")
    high_ranking_employees_names = get_all_names("High_ranking")

    Enron_employers_emails = get_all_emails("Enron")
    ECT_employers_emails = get_all_emails("ECT")
    EES_employers_emails = get_all_emails("EES")
    USA_employers_emails = get_all_emails("USA")
    EU_employers_emails = get_all_emails("EU")
    high_ranking_employees_emails = get_all_emails("High_ranking")

    Enron_employers = Enron_employers_names | Enron_employers_emails
    ECT_employers = ECT_employers_names | ECT_employers_emails
    EES_employers = EES_employers_names | EES_employers_emails
    USA_employers = USA_employers_names | USA_employers_emails
    EU_employers = EU_employers_names | EU_employers_emails
    high_ranking_employees = high_ranking_employees_names | high_ranking_employees_emails
    
def clearData():
    Enron_employers.clear()
    ECT_employers.clear()
    EES_employers.clear()
    USA_employers.clear()
    EU_employers.clear()
    high_ranking_employees.clear()

def learnFromRulesViolated(row):
    rules = row['violated_rules']
    rules_violated = rules.split(",")
    for rule in rules_violated:
        if rule == "2.1":
            ECT_employers.add(row['From'])
            ECT_employers.add(row['X-From'])
            # insert_or_update("ECT", row['X-From'], row['From'])
        if rule == "2.2":
            high_ranking_employees.add(row['From'])
            high_ranking_employees.add(row['X-From'])
            # insert_or_update("High_ranking", row['X-From'], row['From'])
        if rule == "1.3":
            Enron_employers.add(row['From'])    
            Enron_employers.add(row['X-From'])
            # insert_or_update("Enron", row['X-From'], row['From'])
        if rule == "2.3":
            Enron_employers.add(row['From'])    
            Enron_employers.add(row['X-From'])    
            # insert_or_update("Enron", row['X-From'], row['From'])
        

def extract_info_from_email(email_addresses):
    # Define a regex pattern to match the required information
    pattern = r"([\w\s]+)\/([\w]+)\/([\w]+)@([\w]+)"
    
    # Find all occurrences of the pattern in the email addresses
    matches = re.findall(pattern, email_addresses)
    
    extracted_info = []
    for match in matches:
        name = match[0].strip()  # Extract name
        location = match[1].strip()  # Extract location
        company = match[2].strip()  # Extract company
        domain = match[3].strip()  # Extract domain
        
        extracted_info.append((name, location, company, domain))
    
    return extracted_info

def extract_info_from_forword(email_body):
    # Define a regex pattern to match the required information
    pattern = r"Forwarded by ([\w\s/]+)\/([\w\s]+)\/([\w]+) on \d{2}/\d{2}/\d{4}"
    
    # Find all occurrences of the pattern in the email body
    matches = re.findall(pattern, email_body)
    
    extracted_info = []
    for match in matches:
        name = match[0].strip()  # Extract name
        location = match[1].strip()  # Extract location
        company = match[2].strip()  # Extract company
        
        extracted_info.append((name, location, company))
    
    return extracted_info    

def learnFromData(rows):
    for index, row in rows.iterrows():        

        if len(row['violated_rules']) > 0:
            learnFromRulesViolated(row)

        # # Check if the email is from a high ranking employee  
        # if row['From'] is not None and row['X-From'] is not None:
        #     if row['From'].strip() in high_ranking_employees or row['X-From'].strip() in high_ranking_employees:
        #         if 'business' in assign_labels(row['Subject'] + " " + row['email_body']):
        #             if '2.2' not in row['violated_rules']:
        #                 high_ranking_employees.add(row['To'])
        #                 high_ranking_employees.add(row['X-To'])
        #                 # insert_or_update("High_ranking", row['X-To'], row['To'])

        if row['From'] is not None and row['X-From'] is not None:
            if row['From'].strip() in Enron_employers or row['X-From'].strip() in Enron_employers:
                if 'business' in assign_labels(row['Subject'] + " " + row['email_body']) or 'financial' in assign_labels(row['Subject'] + " " + row['email_body']):
                    if '1.3' not in row['violated_rules']:
                        high_ranking_employees.add(row['To'])
                        high_ranking_employees.add(row['X-To'])
                        # insert_or_update("High_ranking", row['X-To'], row['To'])



        
        forworder = extract_info_from_forword(row['email_body'])    
        for idx, info in enumerate(forworder, start=1):
            name = info[0].replace('\n', '')
            if info[2] == "ECT":
                ECT_employers.add(name)
                # insert_or_update("ECT", name, "")
            if info[2] == "EES":
                EES_employers.add(name)
                # insert_or_update("EES", name, "")
            if info[1] == "USA" or info[1] == "US" or info[1] == "HOU":
                USA_employers.add(name)    
                # insert_or_update("USA", name, "")
            if info[1] == "EU" or info[1] == "LON":
                EU_employers.add(name)        
                # insert_or_update("EU", name, "")
            # print(f"Forwarded by {idx}:")
            # print("Name:", name)
            # print("Location:", info[1])
            # print("Company:", info[2])
            # print()
        info_list = extract_info_from_email(row['email_body'])
        for idx, info in enumerate(info_list, start=1):
            name = info[0].replace('\n', '')
            if info[2] == "ECT":
                ECT_employers.add(name)
                # insert_or_update("ECT", name, "")
            if info[2] == "EES":
                EES_employers.add(name)
                insert_or_update("EES", name, "")
            if info[1] == "USA" or info[1] == "US" or info[1] == "HOU":
                USA_employers.add(name)    
                # insert_or_update("USA", name, "")
            if info[1] == "EU" or info[1] == "LON":
                EU_employers.add(name) 
                # insert_or_update("EU", name, "")
            # print(f"Email Address {idx}:")
            # print("Name:", name)
            # print("Location:", info[1])
            # print("Company:", info[2])
            # print("Domain:", info[3])
            # print()

clearData()
emails_train = pd.read_pickle('enron_students.pkl')
# num_rows = emails_train.shape[0]
# print("Number of rows:", num_rows)
rowsToLearn = emails_train.head(51700)
learnFromData(rowsToLearn)

print("ECT Employers len: ", len(ECT_employers))
print("EES Employers len: ", len(EES_employers))
print("USA Employers len: ", len(USA_employers))
print("EU Employers len: ", len(EU_employers))
print("High Ranking Employees len: ", len(high_ranking_employees))

ECT Employers len:  2388
EES Employers len:  542
USA Employers len:  2221
EU Employers len:  395
High Ranking Employees len:  5626


In [263]:
emails_train = pd.read_pickle('enron_students.pkl')

# rowsToLearn = emails_train.head(2000)
rows = emails_train.head(50000)

# learnFromData(rowsToLearn)
# loadFromDB()


# print("Enron Employers:")
# print(Enron_employers)
# print("ECT Employers:")
# print(ECT_employers)
# print("EES Employers:")
# print(EES_employers)
# print("USA Employers:")
# print(USA_employers)
# print("EU Employers:")
# print(EU_employers)
# print("High Ranking Employees:")
# print(high_ranking_employees)

# print("ECT Employers len: ", len(ECT_employers))
# print("EES Employers len: ", len(EES_employers))
# print("USA Employers len: ", len(USA_employers))
# print("EU Employers len: ", len(EU_employers))
# print("High Ranking Employees len: ", len(high_ranking_employees))


# for index, row in rows.iterrows():
#     print(row["From"])
#     print(row["To"])
#     print("--------------------")

# row = emails_train.iloc[145]
# for key, value in row.items():
#     print(key, ":", value)
#     print("--------------------")


sample_email_content = """
From: kevin.ruscitti@enron.com
To: dbehrman@ftenergy.com
Subject: Bid Week Prices
Mail Body:
David,
I have attached a listing of all my Bid Week transactions.
Let me know if you have any questions. 
Kevin Ruscitti
(713) 853-6320

SSN: 123-45-6789
Phone: (555) 555-1234
"""
count_our_blocked = 0
count_real_blocked = 0
count_FP = 0
count_FN = 0

for index, row in rows.iterrows():
    # print(index)
    # for key, value in row.items():
    #     print(key, ":", value)
    #     print("--------------------")
    # print("##########################")  
    # print(index)

    vertict = process_email(row)
    if vertict == False:
        count_our_blocked += 1
    if row['verdict'] == "BLOCK":
        count_real_blocked += 1 
        if vertict == True:
            count_FP += 1
    if row['verdict'] == "ALLOW" and vertict == False:
        count_FN += 1        

        
    print("=========================================================================================")

print("Our blocked emails:", count_our_blocked)
print("Real blocked emails:", count_real_blocked)    
print("Real blocked emails that we approved:", count_FP)
print("Real allowed emails that we blocked:", count_FN)

Financial subject detected!
Financial subject detected!
Financial subject detected!
Their verdict: ALLOW vs our verdict: True
Their Broken Rules:  vs our broken rules: 
Business subject detected!
Business subject detected!
Their verdict: ALLOW vs our verdict: True
Their Broken Rules:  vs our broken rules: 
Their verdict: ALLOW vs our verdict: True
Their Broken Rules:  vs our broken rules: 
Their verdict: ALLOW vs our verdict: True
Their Broken Rules:  vs our broken rules: 
Their verdict: ALLOW vs our verdict: True
Their Broken Rules:  vs our broken rules: 
Their verdict: ALLOW vs our verdict: True
Their Broken Rules:  vs our broken rules: 
Their verdict: ALLOW vs our verdict: True
Their Broken Rules:  vs our broken rules: 
Their verdict: ALLOW vs our verdict: True
Their Broken Rules:  vs our broken rules: 
Their verdict: BLOCK vs our verdict: True
Their Broken Rules: 2, ., 3 vs our broken rules: 
Financial subject detected!
Business subject detected!
Financial subject detected!
Contain

In [257]:

# print("Enron Employers:")
# print(Enron_employers)
# print("ECT Employers:")
# print(ECT_employers)
# print("EES Employers:")
# print(EES_employers)
# print("USA Employers:")
# print(USA_employers)
# print("EU Employers:")
# print(EU_employers)
# print("High Ranking Employees:")
# print(high_ranking_employees)

if 'Jana Giovannini' in ECT_employers:
    print("is in ECT")

is in ECT
